In [1]:
import importlib
import sys, os
sys.path.insert(0, os.path.abspath("../src"))
import lpkit.read_sl1000 as sl1000
import lpkit.langmuir as lp
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = "notebook" 

In [2]:
importlib.reload(sl1000)
importlib.reload(lp)
#npz_file = '../data/CB0020.npz'
npz_file = '../data/20250206-He-plasma-01.npz'
#npz_file = '../data/20250206-He-plasma-preanode.npz'
df, metadata = sl1000.read_npz_file(npz_file)
param = dict(window=[0.59,3],peak_distance=0.095,peak_height=0.01,time_offset=0.05)
#param = dict(window=[0.57,10],peak_distance=0.9,peak_height=0.1,time_offset=0.35)
data = lp.process_lp_data(df,metadata,**param)

In [3]:
importlib.reload(lp)
lp.plot_raw_data_plotly(data,downdampling=10)

In [4]:
importlib.reload(lp)
cur = data['current_filtered']
v = data['voltage_filtered']
mask = data['mask']
im, vm = lp.apply_mask(mask,cur,v)

segments = lp.make_segments(data)
av, ai = lp.average_segments(segments)

In [5]:
factor=10
fig = go.Figure()
fig.add_trace(go.Scattergl(
    x=vm[::factor]*1000,
    y=-im[::factor]*100,
    mode='markers',
    marker=dict(size=2, color='#cffdff'), 
    opacity=0.1,
    name = 'data'
    ))
fig.add_trace(go.Scattergl(x=  av*1000,y = ai*100,name='averaged'))

lp.plotly_style_dark(fig)
fig.show()

In [6]:
importlib.reload(lp)
#vlim = [87, 90]
vlim = [100.5,103]
#vlim = [-1.5,-0.8]
lpv = av*1000
lpi = ai*100
logi = np.log(lpi+np.abs(lpi.min())+1e-3)
#logi = np.sign(lpi)*np.log(np.abs(lpi))
lp.fit_logi(lpv,logi,vlim)

Te = 3.02 eV
